In [1]:
# setup
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import (
    ColumnDataSource, Range1d, DataRange1d, DatetimeAxis,
    TickFormatter, DatetimeTickFormatter, FuncTickFormatter,
    Grid, Legend, Plot, BoxAnnotation, Span, CustomJS, Rect, Circle, Line,
    HoverTool, BoxZoomTool, PanTool, WheelZoomTool,
    WMTSTileSource, LabelSet
    )
from bokeh.models.widgets import DataTable, DateFormatter, TableColumn, Div

import numpy as np
import sys
import os

sys.path.append(os.path.join(os.getcwd(), 'plot_app'))
from pyulog import *
from pyulog.px4 import *
from plotting import *
from config import *
from notebook_helper import *

output_notebook()

Loading BokehJS ...

In [2]:
file_name = '/home/alexandre/Documents/Px4_ws/flight_review/Link to Flight Logs/09-11-17/log_5_2017-11-9-10-21-24.ulg' # TODO: fill in file name
ulog = ULog(file_name)
data = ulog.data_list
px4_ulog = PX4ULog(ulog)
px4_ulog.add_roll_pitch_yaw()
use_downsample = False

print("message names: {:}".format(sorted([d.name for d in data])))
print_ulog_info(ulog)

message names: ['actuator_controls_0', 'actuator_outputs', 'actuator_outputs', 'battery_status', 'commander_state', 'control_state', 'cpuload', 'ekf2_innovations', 'ekf2_timestamps', 'estimator_status', 'input_rc', 'rc_channels', 'sensor_combined', 'sensor_preflight', 'system_power', 'task_stack_info', 'telemetry_status', 'vehicle_attitude', 'vehicle_attitude_setpoint', 'vehicle_command', 'vehicle_global_position', 'vehicle_gps_position', 'vehicle_land_detected', 'vehicle_local_position', 'vehicle_rates_setpoint', 'vehicle_status', 'wind_estimate']
System: PX4
Hardware: PX4FMU_V2
Software Version: d928fd3bb9c7cd264a8587346d49df9ecbee8782
Dropouts: 49 (2.29 s)
Logging duration: 0:03:48


In [3]:
use_downsample = True # you may want to activate this for large logs (But you will not see all samples when zooming in)

In [4]:
# load a dataset to inspect the field names and types
display_message = 'vehicle_global_position'
print('Displaying : ' + display_message)
sensor_data = [ elem for elem in data if elem.name == display_message and elem.multi_id == 0][0]
types_list = [(f.type_str, f.field_name) for f in sensor_data.field_data]
for ftype, fname in types_list: print("{:10s} {:}".format(ftype, fname))

Displaying : vehicle_global_position
uint64_t   timestamp
uint64_t   time_utc_usec
double     lat
double     lon
double     delta_lat_lon[0]
double     delta_lat_lon[1]
float      alt
float      delta_alt
float      vel_n
float      vel_e
float      vel_d
float      pos_d_deriv
float      yaw
float      eph
float      epv
float      evh
float      evv
float      terrain_alt
float      pressure_alt
uint8_t    lat_lon_reset_counter
uint8_t    alt_reset_counter
bool       terrain_alt_valid
bool       dead_reckoning


In [5]:
plot = plot_map(data, plot_config) # gps map
if plot != None: show(plot)

AttributeError: 'list' object has no attribute 'get_dataset'

In [6]:
# plot raw acceleration sensor data
data_plot = DataPlot(data, plot_config, 'sensor_combined',
        y_axis_label = '[m/s^2]', title = 'Raw Acceleration', plot_height = 'normal')
data_plot.add_graph(['accelerometer_m_s2[0]', 'accelerometer_m_s2[1]', 'accelerometer_m_s2[2]'],
                    colors3, ['x', 'y', 'z'], use_downsample=use_downsample)
show(data_plot.finalize())

In [7]:
# a more complex plot with multiple datasets
data_plot = DataPlot(data, plot_config, 'sensor_combined', y_start=0, title = 'Thrust and Magnetic Field',
                     plot_height='normal')
data_plot.add_graph([lambda data: ('len_mag', 
    np.sqrt(data['magnetometer_ga[0]']**2 + data['magnetometer_ga[1]']**2 + data['magnetometer_ga[2]']**2))],
    colors2[0:1], ['Norm of Magnetic Field'], use_downsample=use_downsample)

data_plot.change_dataset('actuator_controls_0')
data_plot.add_graph([lambda data: ('thrust', data['control[3]'])], colors2[1:2], ['Thrust'],
                    use_downsample=use_downsample)

show(data_plot.finalize())

In [8]:
# Approximated Airspeed
global_position = ulog.get_dataset('vehicle_global_position').data
t = global_position['timestamp']
vx = global_position['vel_n']
vy = global_position['vel_e']
v_h = np.sqrt(np.square(vx) + np.square(vy))
heading_global = global_position['yaw']
h_x = np.cos(heading_global)
h_y = np.sin(heading_global)
airspeed = vx*h_x + vy*h_y

local_position = ulog.get_dataset('vehicle_local_position').data
heading_local= local_position['yaw']

p = figure(plot_width = 800, active_scroll='wheel_zoom')
p.line(t, airspeed*3.6, color='red', alpha = 0.8, legend="airspeed")
p.line(t, v_h*3.6, color='green', alpha = 0.5, legend="Horizontal Speed")
show(p)


In [ ]:
# plot low-pass filtered raw acceleration sensor data
from scipy.signal import butter, lfilter
cur_data = ulog.get_dataset('sensor_combined').data
t = cur_data['timestamp']

fs = len(t) / ((t[-1]-t[0])/1e6) # sample rate [Hz]
cutoff = 10 # cutoff freq [Hz]
order = 5
B, A = butter(order, cutoff / (fs / 2), btype='low') # Butterworth low-pass
filtered_signal = lfilter(B, A, cur_data['accelerometer_m_s2[0]'])

p = figure(plot_width = 800, active_scroll='wheel_zoom')
p.line(t, cur_data['accelerometer_m_s2[0]'], color='red', alpha = 0.5)
p.line(t, filtered_signal, color='blue', alpha = 0.8)
show(p)

In [19]:
# get the raw acceleration
sensor_combined = ulog.get_dataset('sensor_combined').data
ax = sensor_combined['accelerometer_m_s2[0]']
ay = sensor_combined['accelerometer_m_s2[1]']
az = sensor_combined['accelerometer_m_s2[2]']
t = sensor_combined['timestamp']

In [20]:
# and plot it
p = figure(plot_width = 800, active_scroll='wheel_zoom')
p.line(t, ax, color='red', alpha = 0.8, legend="accel x")
p.line(t, ay, color='green', alpha = 0.8, legend="accel y")
p.line(t, az, color='blue', alpha = 0.8, legend="accel z")
show(p)

In [ ]:
# select a window
dt = (t[-1]-t[0]) / len(t) / 1e6 # delta t in seconds
start_index = int(20 / dt) # select start of window (seconds): make sure the vehicle is hovering at that point
window_len_s = 3 # window length in seconds
tw=t[start_index:int(start_index+window_len_s/dt)]
axw=ax[start_index:int(start_index+window_len_s/dt)]
ayw=ay[start_index:int(start_index+window_len_s/dt)]
azw=az[start_index:int(start_index+window_len_s/dt)]

In [ ]:
# and plot it
p = figure(plot_width = 800, active_scroll='wheel_zoom')
p.line(tw, axw, color='red', alpha = 0.8, legend="accel x")
p.line(tw, ayw, color='green', alpha = 0.8, legend="accel y")
p.line(tw, azw, color='blue', alpha = 0.8, legend="accel z")
show(p)

In [ ]:
# FFT frequency plot
import scipy
import scipy.fftpack
from scipy import pi

FFT_x = abs(scipy.fft(axw))
FFT_y = abs(scipy.fft(ayw))
FFT_z = abs(scipy.fft(azw))

freqs = scipy.fftpack.fftfreq(len(axw), dt)

p = figure(plot_width = 800, active_scroll='wheel_zoom')
p.line(freqs,20*scipy.log10(FFT_x), color='red', alpha = 0.8, legend="x")
p.line(freqs,20*scipy.log10(FFT_y), color='green', alpha = 0.8, legend="y")
p.line(freqs,20*scipy.log10(FFT_z), color='blue', alpha = 0.8, legend="z")
p.legend.click_policy="hide"
show(p)